In [56]:
import neo4j

import csv

import math
import numpy as np
import pandas as pd

import psycopg2

from decimal import Decimal
from sklearn.preprocessing import StandardScaler

In [57]:
driver = neo4j.GraphDatabase.driver(uri="neo4j://neo4j:7687", auth=("neo4j","ucb_mids_w205"))

In [58]:
session = driver.session(database="neo4j")

In [59]:
def my_neo4j_wipe_out_database():
    "wipe out database by deleting all nodes and relationships"
    
    query = "match (node)-[relationship]->() delete node, relationship"
    session.run(query)
    
    query = "match (node) delete node"
    session.run(query)

In [60]:
def my_neo4j_run_query_pandas(query, **kwargs):
    "run a query and return the results in a pandas dataframe"
    
    result = session.run(query, **kwargs)
    
    df = pd.DataFrame([r.values() for r in result], columns=result.keys())
    
    return df

In [61]:
def my_neo4j_nodes_relationships():
    "print all the nodes and relationships"
   
    print("-------------------------")
    print("  Nodes:")
    print("-------------------------")
    
    query = """
        match (n) 
        return n.name as node_name, labels(n) as labels
        order by n.name
    """
    
    df = my_neo4j_run_query_pandas(query)
    
    number_nodes = df.shape[0]
    
    display(df)
    
    print("-------------------------")
    print("  Relationships:")
    print("-------------------------")
    
    query = """
        match (n1)-[r]->(n2) 
        return n1.name as node_name_1, labels(n1) as node_1_labels, 
            type(r) as relationship_type, n2.name as node_name_2, labels(n2) as node_2_labels
        order by node_name_1, node_name_2
    """
    
    df = my_neo4j_run_query_pandas(query)
    
    number_relationships = df.shape[0]
    
    display(df)
    
    density = (2 * number_relationships) / (number_nodes * (number_nodes - 1))
    
    print("-------------------------")
    print("  Density:", f'{density:.1f}')
    print("-------------------------")
    

In [62]:
def my_neo4j_number_nodes_relationships():
    "print the number of nodes and relationships"
   
    
    query = """
        match (n) 
        return n.name as node_name, labels(n) as labels
        order by n.name
    """
    
    df = my_neo4j_run_query_pandas(query)
    
    number_nodes = df.shape[0]
    
    
    query = """
        match (n1)-[r]->(n2) 
        return n1.name as node_name_1, labels(n1) as node_1_labels, 
            type(r) as relationship_type, n2.name as node_name_2, labels(n2) as node_2_labels
        order by node_name_1, node_name_2
    """
    
    df = my_neo4j_run_query_pandas(query)
    
    number_relationships = df.shape[0]
    
    print("-------------------------")
    print("  Nodes:", number_nodes)
    print("  Relationships:", number_relationships)
    print("-------------------------")


In [63]:
def my_neo4j_create_node(stock_name):
    "create a node with label Stock"
    
    query = """
    
    CREATE (:Stock {name: $stock_name})
    
    """
    
    session.run(query, stock_name=stock_name)
    

In [64]:
def insert_stock_data(tx, stock, date, close, volume):
    """
        Insert stock and trading day nodes into Neo4j
    """
    tx.run("""
        MERGE (s:Stock {name: $stock})
        MERGE (t:StockTradingDay {date:date($date), close:toFloat($close), volume:toInteger($volume)})
        MERGE (s)-[:TRADING_DAY]->(t)
    """, stock=stock, date=date, close=close, volume=volume)

In [65]:
def link_trading_days(tx, stock):
    """
        Links StockTradingDay nodes for a given stock using apoc.nodes.link()
    """
    tx.run("""
        MATCH(s:Stock {name: $stock})-[:TRADING_DAY]->(day:StockTradingDay)
        WITH s, day
        ORDER by day.date ASC
        WITH s, collect(day) AS days
        UNWIND range(0, size(days)-2) AS i
        WITH days[i] AS current_day, days[i+1] AS next_day
        MERGE (current_day)-[:NEXT_DAY]->(next_day)
    """, stock=stock)

In [66]:
connection = psycopg2.connect(
    user = "postgres",
    password = "ucb",
    host = "postgres",
    port = "5432",
    database = "postgres"
)

In [67]:
cursor = connection.cursor()

In [68]:
my_neo4j_wipe_out_database()

In [69]:
my_neo4j_number_nodes_relationships()

-------------------------
  Nodes: 0
  Relationships: 0
-------------------------


In [70]:
connection.rollback()

query = """

select date, open, close, volume, name
from stocks
where date between '2021-05-01' and '2021-12-31'
order by date, name
;

"""

cursor.execute(query)

connection.rollback()

rows = cursor.fetchall()

rows

# for row in rows:
    
#     stock = row[-1]
    
#     my_neo4j_create_node(stock)


[(datetime.date(2021, 5, 3),
  Decimal('132.0399932861328'),
  Decimal('132.5399932861328'),
  Decimal('75135100'),
  'AAPL'),
 (datetime.date(2021, 5, 3),
  Decimal('510.9700012207031'),
  Decimal('503.4599914550781'),
  Decimal('1458600'),
  'ADBE'),
 (datetime.date(2021, 5, 3),
  Decimal('154.0'),
  Decimal('151.32000732421875'),
  Decimal('3265500'),
  'ADI'),
 (datetime.date(2021, 5, 3),
  Decimal('189.1699981689453'),
  Decimal('191.4600067138672'),
  Decimal('1514200'),
  'ADP'),
 (datetime.date(2021, 5, 3),
  Decimal('292.989990234375'),
  Decimal('287.5'),
  Decimal('644600'),
  'ADSK'),
 (datetime.date(2021, 5, 3),
  Decimal('89.06999969482422'),
  Decimal('88.68000030517578'),
  Decimal('2071000'),
  'AEP'),
 (datetime.date(2021, 5, 3),
  Decimal('599.1400146484375'),
  Decimal('599.77001953125'),
  Decimal('633200'),
  'ALGN'),
 (datetime.date(2021, 5, 3),
  Decimal('134.25'),
  Decimal('132.85000610351562'),
  Decimal('7750200'),
  'AMAT'),
 (datetime.date(2021, 5, 3),
  D

In [71]:

for row in rows:
    stock = row[-1]
    date = row[0]
    close = float(row[2]) if isinstance(row[2], Decimal) else row[2]
    volume = int(row[3]) if isinstance(row[3], Decimal) else row[3]

    session.execute_write(insert_stock_data, stock, date, close, volume)

# Link trading day nodes per stock
stocks = set(row[-1] for row in rows)
for stock in stocks:
    session.execute_write(link_trading_days, stock)




In [72]:
my_neo4j_number_nodes_relationships()

-------------------------
  Nodes: 9486
  Relationships: 18666
-------------------------


In [73]:
my_neo4j_nodes_relationships()

-------------------------
  Nodes:
-------------------------


node_name             labels
0         AAPL            [Stock]
1         ADBE            [Stock]
2          ADI            [Stock]
3          ADP            [Stock]
4         ADSK            [Stock]
5          AEP            [Stock]
6         ALGN            [Stock]
7         AMAT            [Stock]
8          AMD            [Stock]
9         AMGN            [Stock]
10        AMZN            [Stock]
11        ANSS            [Stock]
12        ASML            [Stock]
13        ATVI            [Stock]
14        AVGO            [Stock]
15        BIDU            [Stock]
16        BIIB            [Stock]
17        BKNG            [Stock]
18        CDNS            [Stock]
19         CDW            [Stock]
20        CERN            [Stock]
21        CHKP            [Stock]
22        CHTR            [Stock]
23       CMCSA            [Stock]
24        COST            [Stock]
25        CPRT            [Stock]
26        CRWD            [Stock]
27        CSCO            [Stock]
28         CSX            [Stock]
29        CTAS            [Stock]
30        CTSH            [Stock]
31        DLTR            [Stock]
32        DOCU            [Stock]
33        DXCM            [Stock]
34          EA            [Stock]
35        EBAY            [Stock]
36         EXC            [Stock]
37        FAST            [Stock]
38          FB            [Stock]
39        FISV            [Stock]
40         FOX            [Stock]
41        FOXA            [Stock]
42        GILD            [Stock]
43        GOOG            [Stock]
44       GOOGL            [Stock]
45         HON            [Stock]
46        IDXX            [Stock]
47        ILMN            [Stock]
48        INCY            [Stock]
49        INTC            [Stock]
50        INTU            [Stock]
51        ISRG            [Stock]
52          JD            [Stock]
53         KDP            [Stock]
54         KHC            [Stock]
55        KLAC            [Stock]
56        LRCX            [Stock]
57        LULU            [Stock]
58         MAR            [Stock]
59        MCHP            [Stock]
60        MDLZ            [Stock]
61        MELI            [Stock]
62        MNST            [Stock]
63        MRNA            [Stock]
64        MRVL            [Stock]
65        MSFT            [Stock]
66        MTCH            [Stock]
67          MU            [Stock]
68        NFLX            [Stock]
69        NTES            [Stock]
70        NVDA            [Stock]
71        NXPI            [Stock]
72        OKTA            [Stock]
73        ORLY            [Stock]
74        PAYX            [Stock]
75        PCAR            [Stock]
76         PDD            [Stock]
77         PEP            [Stock]
78        PTON            [Stock]
79        PYPL            [Stock]
80        QCOM            [Stock]
81        REGN            [Stock]
82        ROST            [Stock]
83        SBUX            [Stock]
84        SGEN            [Stock]
85        SIRI            [Stock]
86        SNPS            [Stock]
87        SPLK            [Stock]
88        SWKS            [Stock]
89        TCOM            [Stock]
90        TEAM            [Stock]
91        TMUS            [Stock]
92        TSLA            [Stock]
93         TXN            [Stock]
94        VRSK            [Stock]
95        VRSN            [Stock]
96        VRTX            [Stock]
97         WBA            [Stock]
98        WDAY            [Stock]
99         XEL            [Stock]
100       XLNX            [Stock]
101         ZM            [Stock]
102       None  [StockTradingDay]
103       None  [StockTradingDay]
104       None  [StockTradingDay]
105       None  [StockTradingDay]
106       None  [StockTradingDay]
107       None  [StockTradingDay]
108       None  [StockTradingDay]
109       None  [StockTradingDay]
110       None  [StockTradingDay]
111       None  [StockTradingDay]
112       None  [StockTradingDay]
113       None  [StockTradingDay]
114       None  [StockTradingDay]
115       None  [StockTradingDay]
116       None  [StockTradi

-------------------------
  Relationships:
-------------------------


node_name_1      node_1_labels relationship_type node_name_2  \
0            AAPL            [Stock]       TRADING_DAY        None   
1            AAPL            [Stock]       TRADING_DAY        None   
2            AAPL            [Stock]       TRADING_DAY        None   
3            AAPL            [Stock]       TRADING_DAY        None   
4            AAPL            [Stock]       TRADING_DAY        None   
5            AAPL            [Stock]       TRADING_DAY        None   
6            AAPL            [Stock]       TRADING_DAY        None   
7            AAPL            [Stock]       TRADING_DAY        None   
8            AAPL            [Stock]       TRADING_DAY        None   
9            AAPL            [Stock]       TRADING_DAY        None   
10           AAPL            [Stock]       TRADING_DAY        None   
11           AAPL            [Stock]       TRADING_DAY        None   
12           AAPL            [Stock]       TRADING_DAY        None   
13           AAPL            [Stock]       TRADING_DAY        None   
14           AAPL            [Stock]       TRADING_DAY        None   
15           AAPL            [Stock]       TRADING_DAY        None   
16           AAPL            [Stock]       TRADING_DAY        None   
17           AAPL            [Stock]       TRADING_DAY        None   
18           AAPL            [Stock]       TRADING_DAY        None   
19           AAPL            [Stock]       TRADING_DAY        None   
20           AAPL            [Stock]       TRADING_DAY        None   
21           AAPL            [Stock]       TRADING_DAY        None   
22           AAPL            [Stock]       TRADING_DAY        None   
23           AAPL            [Stock]       TRADING_DAY        None   
24           AAPL            [Stock]       TRADING_DAY        None   
25           AAPL            [Stock]       TRADING_DAY        None   
26           AAPL            [Stock]       TRADING_DAY        None   
27           AAPL            [Stock]       TRADING_DAY        None   
28           AAPL            [Stock]       TRADING_DAY        None   
29           AAPL            [Stock]       TRADING_DAY        None   
30           AAPL            [Stock]       TRADING_DAY        None   
31           AAPL            [Stock]       TRADING_DAY        None   
32           AAPL            [Stock]       TRADING_DAY        None   
33           AAPL            [Stock]       TRADING_DAY        None   
34           AAPL            [Stock]       TRADING_DAY        None   
35           AAPL            [Stock]       TRADING_DAY        None   
36           AAPL            [Stock]       TRADING_DAY        None   
37           AAPL            [Stock]       TRADING_DAY        None   
38           AAPL            [Stock]       TRADING_DAY        None   
39           AAPL            [Stock]       TRADING_DAY        None   
40           AAPL            [Stock]       TRADING_DAY        None   
41           AAPL            [Stock]       TRADING_DAY        None   
42           AAPL            [Stock]       TRADING_DAY        None   
43           AAPL            [Stock]       TRADING_DAY        None   
44           AAPL            [Stock]       TRADING_DAY        None   
45           AAPL            [Stock]       TRADING_DAY        None   
46           AAPL            [Stock]       TRADING_DAY        None   
47           AAPL            [Stock]       TRADING_DAY        None   
48           AAPL            [Stock]       TRADING_DAY        None   
49           AAPL            [Stock]       TRADING_DAY        None   
50           AAPL            [Stock]       TRADING_DAY        None   
51           AAPL            [Stock]       TRADING_DAY        None   
52           AAPL            [Stock]       TRADING_DAY        None   
53           AAPL            [Stock]       TRADING_DAY        None   
54           AAPL            [Stock]       TRADING_DAY        None   
55           AAPL            [Stock]       TRADING_DAY        None   
56           AAP

-------------------------
  Density: 0.0
-------------------------


In [74]:
df = pd.DataFrame(rows, columns=['date', 'open', 'close', 'volume', 'name'])

In [75]:
def weighted_corr(x, y, w):
    """
    Compute the weighted Pearson correlation between two series.
    """
    w = np.asarray(w)
    x = np.asarray(x)
    y = np.asarray(y)

    # Weighted means
    w_mean_x = np.average(x, weights=w)
    w_mean_y = np.average(y, weights=w)

    # Weighted covariance and variance
    cov_xy = np.average((x - w_mean_x) * (y - w_mean_y), weights=w)
    var_x = np.average((x - w_mean_x) ** 2, weights=w)
    var_y = np.average((y - w_mean_y) ** 2, weights=w)

    return cov_xy / np.sqrt(var_x * var_y)

def calculate_weighted_correlations(df):
    """
    Compute a weighted correlation matrix based on closing prices and volume.
    """
    pivot_close = df.pivot(index='date', columns='name', values='close')
    pivot_volume = df.pivot(index='date', columns='name', values='volume')

    # Normalize each stock's price series
    scaler = StandardScaler()
    norm_close = pd.DataFrame(
        scaler.fit_transform(pivot_close),
        columns=pivot_close.columns,
        index=pivot_close.index
    )

    stocks = norm_close.columns
    weighted_corr_matrix = pd.DataFrame(index=stocks, columns=stocks, dtype=float)

    for i in range(len(stocks)):
        for j in range(i, len(stocks)):
            s1 = stocks[i]
            s2 = stocks[j]

            valid = norm_close[[s1, s2]].notna().all(axis=1)
            if valid.sum() == 0:
                corr = np.nan
            else:
                # Use average volume as weights
                weights = pivot_volume.loc[valid, [s1, s2]].mean(axis=1)
                x = norm_close.loc[valid, s1]
                y = norm_close.loc[valid, s2]

                corr = weighted_corr(x, y, weights)

            weighted_corr_matrix.loc[s1, s2] = corr
            weighted_corr_matrix.loc[s2, s1] = corr  # symmetric

    return weighted_corr_matrix, list(stocks)

In [76]:
# Insert correlation relationships between stocks into Neo4j
def insert_correlation_data(tx, stock1, stock2, correlation_value):
    """
    Insert correlation relationships between stocks into Neo4j
    """
    tx.run("""
        MATCH (s1:Stock {name: $stock1}), (s2:Stock {name: $stock2})
        MERGE (s1)-[:CORRELATION {value: $correlation_value}]->(s2)
        MERGE (s2)-[:CORRELATION {value: $correlation_value}]->(s1)
    """, stock1=stock1, stock2=stock2, correlation_value=correlation_value)


# Insert correlation relationships for all stock pairs
def insert_all_correlations(weighted_corr_matrix, stock_names, threshold=0.8): # Selected 0.8 correlation to only include strong correlations
    """
    Insert correlations into Neo4j for stock pairs with correlation greater than the threshold.
    """
    for i, stock1 in enumerate(stock_names):
        for j, stock2 in enumerate(stock_names):
            if i < j:
                correlation_value = weighted_corr_matrix.iloc[i, j]
                if abs(correlation_value) >= threshold:
                    session.execute_write(insert_correlation_data, stock1, stock2, correlation_value)


In [77]:
def run_betweenness_tx(tx):
    
    results = []
    
    # Drop the existing graph if it exists
    tx.run("""
        CALL gds.graph.drop('betweenness_graph')
        YIELD graphName
    """)
    
    # Project the graph into Neo4j (with correlation relationships)
    tx.run("""
        CALL gds.graph.project(
            'betweenness_graph', 
            'Stock', 
            'CORRELATION', 
            {relationshipProperties: ['value']}
        )
    """)
    
    result = tx.run("""
        CALL gds.betweenness.stream('betweenness_graph', {relationshipWeightProperty: 'value'})
        YIELD nodeId, score
        RETURN gds.util.asNode(nodeId).name AS name, score as betweenness
        ORDER BY betweenness DESC
    """)

    for record in result:
        results.append({
            'ticker': record['name'],
            'betweenness_score': record['betweenness']
        })
        
    return results

def run_betweenness_centrality():
    """
    Insert betweenness relationships between stocks into Neo4j
    """
    results = session.execute_write(run_betweenness_tx)

    df_betweenness = pd.DataFrame(results)
    
    # Avoid clipping, show the full data output in Jupyter Notebook
    pd.set_option('display.max_rows', None)  
    pd.set_option('display.max_columns', None) 
    pd.set_option('display.width', None) 
    pd.set_option('display.max_colwidth', None)

    df_betweenness.to_csv("betweeness_results_full.csv", index=False)
    
    # Print the DataFrame in Jupyter Notebook
    print(df_betweenness)



In [78]:
correlation_matrix, stock_names = calculate_weighted_correlations(df)
insert_all_correlations(correlation_matrix, stock_names)

run_betweenness_centrality()

    ticker  betweenness_score
0      KHC             5463.0
1     ISRG             5389.0
2     PCAR             5327.0
3      AMD             5255.0
4     ATVI             5185.0
5     COST             5157.0
6     INCY             4977.0
7     TCOM             4975.0
8     PAYX             4901.0
9      PDD             4763.0
10    MRNA             4740.0
11     PEP             4711.0
12     FOX             4592.0
13    IDXX             4495.0
14     WBA             4290.0
15    BIDU             3982.0
16    ORLY             3501.0
17     ADP             3169.0
18    AMGN             2626.0
19    CSCO             2300.0
20     CDW             1630.0
21    ASML             1592.0
22    NTES              822.0
23    CPRT              796.0
24     AEP              710.0
25    VRSK              526.0
26     EXC              460.0
27    TEAM              422.0
28    ILMN              292.0
29    MRVL              286.0
30    AVGO              285.0
31    SPLK              227.0
32    DXCM